In [1]:
import pandas as pd  # Import the pandas library for data manipulation and analysis

import pickle  # Import the pickle module for serialization and deserialization of Python objects

# Lementize
# We use lamentizing in other code that is not presented here.
# We lost relevance of the task when using lamentizing.
# import spacy
# nlp=spacy.load('en_core_web_lg')
# nlp = spacy.load('en_core_web_lg', disable = ['parser','ner'])
# # load_model = spacy.load('en', disable = ['parser','ner'])

from collections import Counter  # Import the Counter class from the collections module for counting occurrences

import numpy as np; np.random.seed(0)  # Import the numpy library for numerical computing and set a random seed for reproducibility

import re  # Import the re module for regular expression support

import io  # Import the io module for input/output operations

import os  # Import the os module for interacting with the operating system

import string  # Import the string module for string manipulation and character sets

import concurrent.futures  # Import the concurrent.futures module for asynchronous execution of functions

import time  # Import the time module for time-related functions

In [ ]:
# Read the Excel file into a DataFrame
Positive = pd.read_excel('Word dictionary.xlsx',sheet_name='Positive')  # Read the 'Positive' sheet from the 'Word dictionary.xlsx' file
F_Positive = pd.read_excel('Word dictionary.xlsx',sheet_name='Fpositive')  # Read the 'Fpositive' sheet from the 'Word dictionary.xlsx' file

# Prepare word lists
words_to_check = Positive['Positive'].astype(str).tolist()  # Convert the 'Positive' column of the 'Positive' DataFrame to a list of strings
words_to_remove = F_Positive['Negative'].astype(str).tolist()  # Convert the 'Negative' column of the 'F_Positive' DataFrame to a list of strings

# Remove spaces from word lists
words_to_check = [word.replace(' ', '') for word in words_to_check]  # Remove spaces from each word in 'words_to_check' list
words_to_remove = [word.replace(' ', '') for word in words_to_remove]  # Remove spaces from each word in 'words_to_remove' list

# Function to parse file name
def parse_file_name(file_name):
    parts = file_name.split('_')  # Split the file name by underscore character
    cik = parts[0]  # Extract the first part as 'cik'
    fillingt = parts[1]  # Extract the second part as 'fillingt'
    date = parts[2]  # Extract the third part as 'date'
    return cik, date, fillingt  # Return the extracted components as a tuple

# Function to clean text
def clean_text(text):
    text = text.replace('\n','')  # Remove newline characters from the text
    text = text.replace('\t','')  # Remove tab characters from the text
    text = text.replace(',', '')  # Remove commas from the text
    text = text.replace('-', '')  # Remove hyphens from the text
    text = text.replace('_', '')  # Remove underscores from the text
    text = text.replace(' ', '')  # Remove spaces from the text
    text = text.lower()  # Convert the text to lowercase
    return text  # Return the cleaned text


In [3]:
# Set the directory containing the files
folder = r'C:\Users\...\10Kfilepath'

# Create a generator expression to iterate over the files in the directory
files = (f for f in os.listdir(folder) if f.endswith('.p'))

# Initialize an empty list to store the results
results = []
def process_file(file):
    # Loop through each file and extract the text
    for file in files:
        
        name = file.replace('.p', '')
                    
        # Get the first and second parts of the filename
        
        cik, date, fill = parse_file_name(name)

        # Open the file in read mode
        with open(os.path.join(folder, file), 'rb') as f:
            # Create a BeautifulSoup object if the file is HTML
            start_time1 = time.time()

            data = pickle.load(f)
            extracted_text = str(data)
            wrd='N/A'
                        
            #extracted_text = test_trans(extracted_text)
            extracted_text = clean_text(extracted_text)
            has_word = 0

            for wod in words_to_remove:
                extracted_text = extracted_text.replace(wod, '')
                
            for wd in words_to_check:
                if wd in extracted_text:
                    has_word = 1
                    wrd = wd
                    break
            
            # Add the filename and has_word flag to the results list
            results.append([cik,date,fill,has_word,wrd])
            elapsed_time1 = time.time() - start_time1
            print(f"✅Processed {date}: in {elapsed_time1:.2f} seconds: Hedge = {has_word} {wrd}")

In [4]:
# Use ThreadPoolExecutor to execute process_file function concurrently
with concurrent.futures.ThreadPoolExecutor() as executor:
    # Map the process_file function to each file in the directory
    executor.map(process_file, os.listdir(folder))

✅Processed 20050513: in 5.96 seconds: Hedge = 0 N/A or N/A
✅Processed 20051109: in 9.31 seconds: Hedge = 0 N/A or N/A✅Processed 20040806: in 9.82 seconds: Hedge = 0 N/A or N/A

✅Processed 20050812: in 8.30 seconds: Hedge = 0 N/A or N/A
✅Processed 20040506: in 10.64 seconds: Hedge = 0 N/A or N/A
✅Processed 20060508: in 13.62 seconds: Hedge = 0 N/A or N/A
✅Processed 20070509: in 16.68 seconds: Hedge = 0 N/A or N/A
✅Processed 20071108: in 17.59 seconds: Hedge = 0 N/A or N/A
✅Processed 20070807: in 20.54 seconds: Hedge = 0 N/A or N/A
✅Processed 20081107: in 14.84 seconds: Hedge = 0 N/A or N/A
✅Processed 20150210: in 27.47 seconds: Hedge = 0 N/A or N/A
✅Processed 20080225: in 27.64 seconds: Hedge = 0 N/A or N/A
✅Processed 20040312: in 28.04 seconds: Hedge = 0 N/A or N/A
✅Processed 20110223: in 28.31 seconds: Hedge = 0 N/A or N/A
✅Processed 20090225: in 29.20 seconds: Hedge = 0 N/A or N/A
✅Processed 20080806: in 17.77 seconds: Hedge = 0 N/A or N/A
✅Processed 20130219: in 30.33 seconds: Hedge

In [5]:
# Create a Pandas DataFrame from the results list
hedge = pd.DataFrame(results, columns=['CIK','Date','filling type', 'Hedge','word found'])
hedge['Date'] = pd.to_datetime(hedge['Date'],format='%Y%m%d').dt.strftime('%Y-%m-%d')
hedge['CIK']=hedge['CIK'].astype(int)
hedge.to_csv('Hedge.csv', index=False)

CIK      Date filling type  Hedge                       word found  \
0      1000180  20050513         10-Q      0                              N/A   
1      1000180  20051109         10-Q      0                              N/A   
2      1000180  20040806         10-Q      0                              N/A   
3      1000180  20050812         10-Q      0                              N/A   
4      1000180  20040506         10-Q      0                              N/A   
...        ...       ...          ...    ...                              ...   
57491     9892  20111026         10-Q      1           interestratederivative   
57492     9892  20170728         10-Q      1  forwardstartinginterestrateswap   
57493     9892  20170427         10-Q      1  forwardstartinginterestrateswap   
57494    98362  20190501         10-Q      0                              N/A   
57495     9892  20060223         10-K      0                              N/A   

      negative word  
0               N/A  
1               N/A  
2               N/A  
3               N/A  
4               N/A  
...             ...  
57491           N/A  
57492           N/A  
57493           N/A  
57494           N/A  
57495           N/A  

[57496 rows x 6 columns]

###  We Import Gurkaynaks hedge to compare with our results below

In [ ]:
gur_hedge=pd.read_csv('..\Data\Excel xlsx and csv\Final Download\hedgedatagurkaynak.csv')
gur_hedge.rename(columns={'filingdate' : 'Date'},inplace=True)
gur_hedge['Date'] = pd.to_datetime(gur_hedge['Date'],format='%d/%m/%Y').dt.strftime('%Y-%m-%d')
gur_hedge['gvkey']=gur_hedge['gvkey'].astype(int)
gur_hedge.drop(columns=['hedge1'],inplace=True)

### We combine our data with funamental data from WRDS to identify our sample with gvkeys instead of CIK numbers as used in Edgar filings. Gurkaynak used gvkeys. We use CIK numbers

In [ ]:
Fundamentals_raw = pd.read_csv('..\Data\Excel xlsx and csv\Final Download\Fundamentals.csv')
Fundamentals_raw= Fundamentals_raw[['gvkey','cik']]
Fundamentals_raw.drop_duplicates(inplace=True)
Fundamentals_raw.dropna(inplace=True)
Fundamentals_raw=Fundamentals_raw.astype(int)
test_hedges=pd.merge(hedge,Fundamentals_raw,how='inner',right_on='cik',left_on='CIK')
test_hedges['Date'] = pd.to_datetime(test_hedges['Date'],format='%Y-%m-%d').dt.strftime('%Y-%m-%d')
test_hedges 

### Comparing the two datasets

In [ ]:
Comparison = pd.merge(test_hedges, gur_hedge, on=['gvkey', 'Date'],how='inner')
Comparison.sort_values(by=['cik','Date'], inplace=True)
Comparison.to_csv('..\Data\Excel xlsx and csv\Final produced\hedgecompare.csv', index=False)

### Below we test out the weight of negative and positive findings that are dissimilar from Gurkaynack

In [ ]:

positivefind=Comparison[(Comparison['Hedge'] != Comparison['hedge2']) & (Comparison['Hedge'] == 1)]
negativefind=Comparison[(Comparison['Hedge'] != Comparison['hedge2']) & (Comparison['Hedge'] != 1)]